# Max activating examples for 10.7 (by norm projection to logits)

Want to see where head 10.7 is most useful!

In [1]:
from transformer_lens.cautils.notebook import *

/home/ubuntu/Transformerlens/transformer_lens/__init__.py:4: UserWarning: Doing ACCELERATE_DISABLE_RICH ...
  warnings.warn("Doing ACCELERATE_DISABLE_RICH ...")
/home/ubuntu/.local/lib/python3.8/site-packages/pandas/core/computation/expressions.py:20: UserWarning: Pandas requires version '2.7.3' or newer of 'numexpr' (version '2.7.1' currently installed).
  from pandas.core.computation.check import NUMEXPR_INSTALLED
/home/ubuntu/Transformerlens/transformer_lens/cautils/notebook.py:11: UserWarning: Running load_ext autoreload...
  warnings.warn("Running load_ext autoreload...")
/home/ubuntu/Transformerlens/transformer_lens/cautils/utils.py:9: UserWarning: Setting grad enabled false...
  warnings.warn("Setting grad enabled false...")


In [17]:
from transformer_lens.rs.callum.max_activating_exploration import print_best_outputs

In [2]:
model = HookedTransformer.from_pretrained("gpt2-small", device=device)
model.set_use_attn_result(True)

Using pad_token, but it is not set yet.


Loaded pretrained model gpt2-small into HookedTransformer


In [3]:
data = get_webtext(seed=5)

Found cached dataset openwebtext-10k (/home/ubuntu/.cache/huggingface/datasets/stas___openwebtext-10k/plain_text/1.0.0/3a8df094c671b4cb63ed0b41f40fb3bd855e9ce2e3765e5df50abcdfb5ec144b)


  0%|          | 0/1 [00:00<?, ?it/s]

In [4]:
LAYER_IDX, HEAD_IDX = (10, 7)
W_U = model.W_U.clone()
HEAD_HOOK_NAME = utils.get_act_name("result", LAYER_IDX)

NUM_PROMPTS = 100
BATCH_SIZE = 10

In [5]:
def hook_to_ablate_head(head_output: Float[Tensor, "batch seq_len head_idx d_head"], hook: HookPoint, head = (LAYER_IDX, HEAD_IDX)):
    assert head[0] == hook.layer()
    assert "result" in hook.name
    head_output[:, :, head[1], :] = 0
    return head_output

## How does 10.7 affect the logits when it's ablated?

We can see cross-entropy loss increases by 0.01 on average when this head is ablated. That might seem like not a lot, but it's actually not far off distribution to other late-stage heads.

In [6]:
str_token_list = []
loss_list = []
ablated_loss_list = []

for i in tqdm(range(NUM_PROMPTS)):
    # new_str = data[BATCH_SIZE * i: BATCH_SIZE * (i + 1)]
    new_str = data[i]
    new_str_tokens = model.to_str_tokens(new_str)
    tokens = model.to_tokens(new_str)
    # tokens = t.stack(tokens).to(device)
    loss = model(tokens, return_type="loss", loss_per_token=True)
    ablated_loss = model.run_with_hooks(tokens, return_type="loss", loss_per_token=True, fwd_hooks=[(HEAD_HOOK_NAME, hook_to_ablate_head)])
    loss_list.append(loss)
    ablated_loss_list.append(ablated_loss)
    str_token_list.append(new_str_tokens)


all_loss = t.cat(loss_list, dim=-1).squeeze()
all_ablated_loss = t.cat(ablated_loss_list, dim=-1).squeeze()

hist(
    all_ablated_loss - all_loss,
    title="Difference in loss after ablating (positive ⇒ loss increases)",
    labels={"x": "Difference in cross-entropy loss"},
    template="simple_white",
    add_mean_line=True,
    width=1000,
    nbins=200
)

  0%|          | 0/100 [00:00<?, ?it/s]

In [32]:
total_num_tokens = sum(len(i) for i in str_token_list)
top_half_pct = int(total_num_tokens * 0.005)


def find_best_improvements(str_token_list, loss_list, ablated_loss_list, k = 15, print_table = False):

    best_loss_decrease = []
    best_text = []
    best_indices = []

    for i, (stl, ll, all) in enumerate(zip(str_token_list, loss_list, ablated_loss_list)):

        loss_diff = (all - ll).squeeze()
        k_actual = min(k, loss_diff.shape[0])
        max_loss_decrease = loss_diff.topk(k_actual, largest=True)
        
        for value, index in zip(max_loss_decrease.values, max_loss_decrease.indices):
            text = stl[max(0, index - 15): index + 2]
            # ! Why `:idx+2` ? Because loss_diff[idx] is large, meaning we failed to predict the `idx+1`-th element, so this should be the last one in our list. We're highlighting the thing we predicted wrong.
            if text:
                text[-1] = f"[bold dark_orange u]{repr(text[-1])}[/]"
                text = "".join(text)
                if "�" not in text:
                    best_loss_decrease.append(value)
                    best_text.append(text + "\n\n")
                    best_indices.append((i, index.item()))

    table = Table("CE-Loss Decrease", "Prompt", title="Prompts & Answers:")

    best_k_indices = []
    best_k_loss_decrease = []
    for loss, text, idx in sorted(zip(best_loss_decrease, best_text, best_indices), key=lambda x: x[0], reverse=True)[:k]:
        table.add_row(f"{loss:.3f}", text)
        best_k_indices.append(idx)
        best_k_loss_decrease.append(loss.item())

    if print_table: rprint(table)

    return best_k_indices, best_k_loss_decrease

best_k_indices, best_k_loss_decrease = find_best_improvements(str_token_list, loss_list, ablated_loss_list, k=top_half_pct)

In [36]:
print_best_outputs(
    best_k_indices,
    best_k_loss_decrease,
    hook = (HEAD_HOOK_NAME, hook_to_ablate_head),
    model = model,
    data = data,
    n = 10,
    random = True
)

<|endoftext|>Astronomy Picture of the Day Discover the cosmos! Each day a different image or photograph of our 
fascinating universe is featured, along with a brief explanation written by a professional astronomer. 2009 January
16ISS: Reflections of EarthCredit & Copyright: Ralf VandeberghExplanation: Remarkable details are visible in this 
view of the orbiting International Space Station (ISS), recorded with a small telescope on planet Earth through a 
clear twilight sky. Seen on December 27th at about 75 degrees elevation and some 350 kilometers above the planet's 
surface, parts of the station, including the Kibo and Columbus science modules, even seem to reflect the Earth's 
lovely bluish colors. The image also shows off large power generating solar arrays on the station's 90 meter long 
integrated truss structure Just put your cursor over the picture to identify some of the major parts of the ISS.

                      Correct = ' ISS', Loss decrease from NNMH = 0.685                       
┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Original                                     ┃ Ablated                                     ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ Top words:                                   │ Top words:                                  │
│                                              │                                             │
│ logit = 17.107 | prob = 0.603 | ' station'   │ logit = 18.438 | prob = 0.837 | ' station'  │
│ logit = 14.363 | prob = 0.039 | ' ISS'       │ logit = 14.680 | prob = 0.020 | ' ISS'      │
│ logit = 13.319 | prob = 0.014 | ' image'     │ logit = 13.317 | prob = 0.005 | ' stations' │
│ logit = 13.103 | prob = 0.011 | ' solar'     │ logit = 13.298 | prob = 0.005 | ' Station'  │
│ logit = 12.868 | prob = 0.009 | ' structure' │ logit = 13.226 | prob = 0.005 | ' system'   │
│                                              │                                             │
│ Correct word (predicted at posn 2):          │ Correct word (predicted at posn 2):         │
│                                              │                                             │
│ logit = 14.363 | prob = 0.039 | ' ISS'       │ logit = 14.680 | prob = 0.020 | ' ISS'      │
└──────────────────────────────────────────────┴─────────────────────────────────────────────┘

directors subsequently told him the board would have no further contact with him. Tasse said he and the other 
supplier have made continued attempts to contact the board to no avail. Tasse alleges that the $10,000 deposit 
cheque he was provided has bounced.Production manager Provost said he deposited the nearly $24,000 cheque from the 
festival into his own account before buying the alcohol for the festival weekend. It wasn��t until the following 
Wednesday that he learned his account was overdrawn by about $15,000 because the cheque never cleared.��I��m 
devastated and I��m broke,�� said Provost, who said he volunteered his time to run the production and used his 
connections to book the performers.Provost said he last spoke with Capital Pride��s treasurer on Aug. 26.��We sent 
multiple emails, we tried calling them for multiple days after that, and there was no answer. No one returned our 
email,�� said

                Correct = ' No', Loss decrease from NNMH = 1.214                 
┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Original                              ┃ Ablated                               ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ Top words:                            │ Top words:                            │
│                                       │                                       │
│ logit = 17.202 | prob = 0.255 | '�'   │ logit = 19.288 | prob = 0.733 | '�'   │
│ logit = 16.837 | prob = 0.177 | ' We' │ logit = 16.612 | prob = 0.050 | ' We' │
│ logit = 16.247 | prob = 0.098 | ' I'  │ logit = 16.425 | prob = 0.042 | ' �'  │
│ logit = 15.918 | prob = 0.071 | '\n'  │ logit = 16.144 | prob = 0.032 | ' I'  │
│ logit = 15.062 | prob = 0.030 | ' It' │ logit = 15.732 | prob = 0.021 | '\n'  │
│                                       │                                       │
│ Correct word (predicted at posn 16):  │ Correct word (predicted at posn 19):  │
│                                       │                                       │
│ logit = 13.539 | prob = 0.007 | ' No' │ logit = 13.354 | prob = 0.002 | ' No' │
└───────────────────────────────────────┴───────────────────────────────────────┘

<|endoftext|>Fuqua Development has unveiled tentative plans for a major mixed-use development wedged against 
Memorial Drive and the Beltline corridor.A new marketing flyer released by the controversial developer elaborates 
on his planned project in Reynoldstown, which includes more than 100,000 square feet of retail and restaurant space
— including (potentially) a CineBistro and Sprouts — plus 120,000 square feet of offices, 600 apartments, and 100 
condos.Fuqua purchased the site at 905 Memorial Drive last year, which didn't thrill a lot of folks, given the 
developer's penchant for big-box projects. Fuqua's planned overhaul will replace a warehouse facility butted up 
against Interstate 20.According to this rendering, which might not represent the latest version of Fuqua's plans, 
retail spaces would front the Beltline, helping to tie the development to

...

                 Correct = ' live', Loss decrease from NNMH = 0.992                  
┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Original                                ┃ Ablated                                 ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ Top words:                              │ Top words:                              │
│                                         │                                         │
│ logit = 20.035 | prob = 0.520 | ' use'  │ logit = 20.531 | prob = 0.660 | ' use'  │
│ logit = 18.729 | prob = 0.141 | ' don'  │ logit = 18.500 | prob = 0.087 | ' don'  │
│ logit = 17.456 | prob = 0.039 | "'re"   │ logit = 17.294 | prob = 0.026 | ' do'   │
│ logit = 17.384 | prob = 0.037 | ' do'   │ logit = 17.294 | prob = 0.026 | "'re"   │
│ logit = 16.805 | prob = 0.021 | ' just' │ logit = 16.629 | prob = 0.013 | ' just' │
│                                         │                                         │
│ Correct word (predicted at posn 32):    │ Correct word (predicted at posn 58):    │
│                                         │                                         │
│ logit = 14.313 | prob = 0.002 | ' live' │ logit = 13.579 | prob = 0.001 | ' live' │
└─────────────────────────────────────────┴─────────────────────────────────────────┘

<|endoftext|>Senators send letter to Roger GoodellSteve Delsohn reports the details surrounding the domestic 
violence charge against Panthers DE Greg Hardy.Sixteen

                  Correct = ' Panthers', Loss decrease from NNMH = 0.999                   
┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Original                                   ┃ Ablated                                    ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ Top words:                                 │ Top words:                                 │
│                                            │                                            │
│ logit = 19.443 | prob = 0.609 | ' Roger'   │ logit = 20.221 | prob = 0.765 | ' Roger'   │
│ logit = 16.925 | prob = 0.049 | ' the'     │ logit = 17.451 | prob = 0.048 | ' Goodell' │
│ logit = 16.818 | prob = 0.044 | ' Goodell' │ logit = 16.931 | prob = 0.028 | ' the'     │
│ logit = 16.434 | prob = 0.030 | ' former'  │ logit = 16.122 | prob = 0.013 | ' former'  │
│ logit = 16.339 | prob = 0.027 | ' NFL'     │ logit = 16.080 | prob = 0.012 | ' NFL'     │
│                                            │                                            │
│ Correct word (predicted at posn 461):      │ Correct word (predicted at posn 575):      │
│                                            │                                            │
│ logit = 9.996 | prob = 0.000 | ' Panthers' │ logit = 9.548 | prob = 0.000 | ' Panthers' │
└────────────────────────────────────────────┴────────────────────────────────────────────┘

of Cadets StatementThe Office of the Commandant and the Corps of Cadets are deeply saddened to hear of the passing
of Reveille VII, the former ��First Lady of Aggieland�� today in College Station. As Aggies we are all very proud 
of our mascot, and we have great respect for her and all the tradition that she represents. We in the Corps of 
Cadets are especially fond of Reveille, as she has been part of the Corps from the beginning, lives with the Corps 
every day as a member of Company E-2, marches with the Corps at all march-ins and parades, and is the highest 
ranking member of the Corps of Cadets. We will remember with great fondness all the joy that Reveille VII brought 
to all Aggies during her time as our mascot, and will remember her excited barks every time our football team 
scored a touchdown. We know that she will continue to do so in the future as she joins the other Reveilles in the 
North end of Kyle Field

                    Correct = ' Reve', Loss decrease from NNMH = 0.838                     
┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Original                                   ┃ Ablated                                    ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ Top words:                                 │ Top words:                                 │
│                                            │                                            │
│ logit = 14.635 | prob = 0.139 | ' Agg'     │ logit = 14.214 | prob = 0.106 | ' Agg'     │
│ logit = 14.406 | prob = 0.110 | ' members' │ logit = 14.188 | prob = 0.103 | ' members' │
│ logit = 13.332 | prob = 0.038 | ' Cad'     │ logit = 13.031 | prob = 0.032 | ' top'     │
│ logit = 12.955 | prob = 0.026 | ' top'     │ logit = 12.967 | prob = 0.030 | ' Texas'   │
│ logit = 12.889 | prob = 0.024 | ' Texas'   │ logit = 12.945 | prob = 0.030 | ' Cad'     │
│                                            │                                            │
│ Correct word (predicted at posn 2435):     │ Correct word (predicted at posn 4257):     │
│                                            │                                            │
│ logit = 5.759 | prob = 0.000 | ' Reve'     │ logit = 4.772 | prob = 0.000 | ' Reve'     │
└────────────────────────────────────────────┴────────────────────────────────────────────┘

In [20]:
k

print_best_outputs(
    best_k_indices,
    best_k_loss_decrease,
    hook = (HEAD_HOOK_NAME, hook_to_ablate_head),
    model = model,
    data = data,
    n = 10,
    random = True
)

NameError: name 'k' is not defined